In [2]:
import numpy as np
import nengo
import nengo_dl
import numpy as np
import tensorflow as tf

# example of a model defined with the functional api
from tensorflow.keras import Model
from tensorflow.keras import Input
from tensorflow.keras.layers import Dense


physical_devices = tf.config.experimental.list_physical_devices("GPU")
if len(physical_devices) > 0:
    tf.config.experimental.set_memory_growth(physical_devices[0], True)
    print("Called tf.config.experimental.set_memory_growth(GPU0, True)")

    
    

x_train = np.array([[ 8.30177453e-01,  6.47933568e-01,  3.40241822e-02,
         1.01843325e+00,  4.13618851e-01, -3.74720000e-13,
        -9.99810000e-13,  1.28209690e+00,  1.12126093e+00,
        -1.38628745e+00, -1.34866950e+00,  8.61870122e+00,
        -4.40466000e-12, -1.10542800e-11,  4.34139614e-01,
        -2.10700000e-01,  3.76046899e-01],
       [ 7.06554129e-01,  1.20582573e-01, -3.59492977e-01,
         1.74993339e+00,  1.38680216e+00,  4.15550000e-13,
        -2.41701000e-12, -1.44823945e-04, -1.66073319e+00,
        -1.20254451e+00,  1.35740917e+00,  7.28939436e-01,
         3.72129000e-12, -1.11408700e-11,  2.57550052e-01,
        -2.10700000e-01,  3.05255872e-01],
       [ 7.03410320e-01,  5.27369601e-01,  1.98364434e-01,
         1.30315585e+00,  4.37237444e-01,  7.54000000e-15,
         3.20700000e-14,  3.71097153e-01,  2.22618216e-01,
         1.52909040e+00, -3.14743626e+00, -4.21084685e+01,
         5.01090000e-13,  4.34930000e-13,  5.38192968e-01,
        -2.10700000e-01,  2.48538933e-01]])

y_train = np.array([[0.        , 0.        , 0.02125402, 0.        , 0.        ,
        0.4945061 , 0.        , 0.        ],
       [0.20280248, 0.12362794, 0.14823406, 0.        , 0.65688647,
        0.        , 0.41601747, 0.27834346],
       [0.26879901, 0.        , 0.        , 0.54751856, 0.54506896,
        0.4137848 , 0.        , 0.1601601 ]])

y_test = np.array([[0.90580905, 0.        , 0.76981722, 0.        , 0.        ,
        0.        , 0.19064948, 0.        ],
       [0.93276146, 0.        , 0.        , 0.        , 0.        ,
        0.67749052, 0.03124749, 0.        ],
       [0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        ]])


x_test = np.array([[ 8.07819557e-01, -7.49590493e-02, -2.13511870e-01,
         1.94799770e+00,  1.29080008e+00, -1.28660000e-12,
        -2.72680000e-12,  6.67107247e-01, -1.05283590e+00,
        -3.62812000e-01,  8.61647602e-01,  1.44303509e+00,
        -4.37790000e-12, -8.51820000e-12,  2.39275139e-01,
        -2.10700000e-01,  2.23918925e-01],
       [ 7.67624866e-01,  5.24348029e-01,  4.29228026e-02,
         1.21681125e+00,  6.32028609e-01,  2.97000000e-14,
        -2.26300000e-13,  1.48807758e+00,  1.97667147e-01,
        -1.29651434e+00, -2.10977928e+00, -1.54732700e+01,
         3.05720000e-12,  9.29700000e-13,  4.99663346e-01,
        -2.10700000e-01,  1.31739821e-01],
       [ 6.63267671e-01,  4.31173369e-01,  3.37241346e-01,
         1.59415650e+00,  9.96488352e-02,  1.00000000e-15,
        -1.30000000e-14, -5.15703100e-01, -1.51941365e+00,
         1.08803955e+00,  2.31445353e+00,  1.07662262e+01,
        -2.99700000e-13, -9.10000000e-13,  2.56518205e-01,
        -2.10700000e-01,  1.62653899e-01]])


# ===== KERAS MODEL =====
x_in = tf.keras.Input(shape=(17,))
x1 = tf.keras.layers.Dense(1000)(x_in)
x2 = Dense(100,  name = 'input_2')(x1)
x_out = Dense(8)(x2)
# define the model
model = Model(inputs=x_in, outputs=x_out)

model.compile(optimizer='adam', loss='mse', metrics=["accuracy"])
model.fit(x_train, y_train, batch_size=12, epochs=20)

print(
    "Accuracy in Keras simulator: {}".format(
        model.evaluate(
            x_test[:, 0:17],
            y_test[:, 0:17],
        )
    )
)
# ===== KERAS MODEL =====
print()

# ===== NengoDL Layer Model ======


with nengo.Network(seed=0) as net:

    net.config[nengo.Ensemble].max_rates = nengo.dists.Choice([100])
    net.config[nengo.Ensemble].intercepts = nengo.dists.Choice([0])
    net.config[nengo.Connection].synapse = None
    neuron_type = nengo.LIF(amplitude=0.01)

    nengo_dl.configure_settings(stateful=False)

    inp = nengo.Node(np.zeros(8))

    # add the first rec layer
    x = nengo_dl.Layer(tf.keras.layers.Dense(units = 17))(inp)
    x = nengo_dl.Layer(neuron_type)(x)

    # add the second rec layer
    x = nengo_dl.Layer(tf.keras.layers.Dense(units= 1000))(x)
    x = nengo_dl.Layer(neuron_type)(x)

    # linear readout
    out = nengo_dl.Layer(tf.keras.layers.Dense(units=8))(x)

    out_p = nengo.Probe(out, label="out_p")
    out_p_filt = nengo.Probe(out, synapse=0.1, label="out_p_filt")
    
    
with nengo_dl.Simulator(net, minibatch_size=20) as sim:
    sim.run(1.0)    
    
    
_, axes = plt.subplots(1, 20, figsize=(20, 4.8))
for i in range(20):
    plot(sim, ax=axes[i], idx=i)

D:\anaconda\lib\site-packages\tensorboard\compat\tensorflow_stub\dtypes.py:541: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
D:\anaconda\lib\site-packages\tensorboard\compat\tensorflow_stub\dtypes.py:542: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
D:\anaconda\lib\site-packages\tensorboard\compat\tensorflow_stub\dtypes.py:543: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
D:\anaconda\lib\site-packages\tensorboard\compat\tensorflow_stub\dtypes.py:544: FutureWarning: Passing (type, 1) or '1type' 

Epoch 1/20
1/1 [==============================] - 0s 459ms/step - loss: 3.3328 - accuracy: 0.0000e+00
Epoch 2/20
1/1 [==============================] - 0s 3ms/step - loss: 11.3238 - accuracy: 0.0000e+00
Epoch 3/20
1/1 [==============================] - 0s 2ms/step - loss: 3.2810 - accuracy: 0.0000e+00
Epoch 4/20
1/1 [==============================] - 0s 3ms/step - loss: 2.2024 - accuracy: 0.3333
Epoch 5/20
1/1 [==============================] - 0s 3ms/step - loss: 4.0900 - accuracy: 0.3333
Epoch 6/20
1/1 [==============================] - 0s 3ms/step - loss: 3.8251 - accuracy: 0.3333
Epoch 7/20
1/1 [==============================] - 0s 4ms/step - loss: 2.1287 - accuracy: 0.3333
Epoch 8/20
1/1 [==============================] - 0s 3ms/step - loss: 1.0395 - accuracy: 0.6667
Epoch 9/20
1/1 [==============================] - 0s 5ms/step - loss: 1.2223 - accuracy: 0.6667
Epoch 10/20
1/1 [==============================] - 0s 6ms/step - loss: 1.9579 - accuracy: 0.6667
Epoch 11/20
1/1 [=======